In [1]:
import pickle 
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt 
import seaborn as sns
import re
%matplotlib inline
%config InlineBackend.figure_formats = {'png', 'retina'}

from sklearn.naive_bayes import MultinomialNB
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score
from sklearn.model_selection import KFold, cross_val_score


## 뉴스 기사를 이용한 성별 선호도 분류 

#### Data Loading 

- DataFrame has four columns, "Date", "Title", "sex", "Body" 

In [2]:
with open("../Data/article.bin", 'rb') as f :
    df = pickle.load(f)
df.tail()

df = df[["Body", "sex"]]

In [3]:
df.tail()

Body  sex
18167  [오마이뉴스 글:문운주, 편집:김지현]【오마이뉴스는 개인의 일상을 소재로 한 생활글...  1.0
18168  음식점[연합뉴스DB]          (세종=연합뉴스) 김수현 기자 = 가계의 주머...  1.0
18169  문재인 정부의 경제 라인에 ‘변양균-장하성’ 양강구도가 형성되는 기류가 나타나고 있...  1.0
18170  A(40)씨는 "형제, 자매는 사이가 좋지 않으면 되레 남보다도 못하다"며 "특히 ...  1.0
18171  국정농단 사건의 주범인 최순실씨 일가의 은닉 재산을 국가로 환수하기 위한 ‘박근혜 ...  1.0

#### Dataset split 

- 80% -> Training 
- 20% -> Test

In [4]:
def dataset_split(df):
    """
    Split df to train/test 
    
    Argument :
    df = pandas.DataFrame
    return : 
    Trainset, Testset
    """
    idx = np.arange(df.shape[0])
    np.random.shuffle(idx)
    train_idx = idx[:int(df.shape[0]*0.8)]
    test_idx = idx[int(df.shape[0]*0.8):]
    
    train_df = df.loc[train_idx]
    test_df = df.loc[test_idx]
    
    return train_df, test_df 

train_df, test_df = dataset_split(df)

In [5]:
test_df.tail()

Body  sex
10143  [편집자주] 당사자에게 직접 묻기 곤란했던 질문들… 독자들의 고민 해결을 위해 기자...  0.0
10829  우리나라 성인 약 93%, 비타민D 부족국내산 축산물과 적절한 야외활동을 통한 결핍...  1.0
2007   김성태, '중앙당 해체와 혁신위한 구태청산' (서울=연합뉴스) 김주형 기자 = 자유...  0.0
6019   악수하는 조명균-리선권 (파주=연합뉴스) 조명균 통일부장관과 리선권 조국평화통일위원...  0.0
12068  사진출처 = 게티이미지뱅크          [아시아경제 씨쓰루 ] 우리가 쉽게 사용...  1.0

###  Soynlp를 이용한 Text 전처리 

- [Soynlp github link](https://github.com/lovit/soynlp)


> 먼저 Tokenizer로써 사용해보겠다. 

> - 크로링한 데이터가 기사임을 감안하여, 띄어쓰기가 잘 되어있다고 생각 할 수 있다. 따라서 패키지 소개페이지에 나온 것처럼 띄어 쓰기가 잘 되어 있는 텍스트 데이터에 대해 토크나이징을 잘 해주는 LTokenizer를 사용하겠다. 
* 아래는 패키지 github page의 내용 
>> WordExtractor 로부터 단어 점수를 학습하였다면, 이를 이용하여 단어의 경계를 따라 문장을 단어열로 분해할 수 있습니다


##### WordTractor로 부터 단어 점수 학습 하기 

- WordExtractor가 계산하는 것은 다양한 종류의 단어 가능 점수들입니다. 이를 잘 조합하여 원하는 점수를 만들 수도 있습니다. 즐겨쓰는 방법 중 하나는 cohesion_forward에 right_branching_entropy를 곱하는 것으로, (1) 주어진 글자가 유기적으로 연결되어 함께 자주 나타나고, (2) 그 단어의 우측에 다양한 조사, 어미, 혹은 다른 단어가 등장하여 단어의 우측의 branching entropy가 높다는 의미입니다.

In [8]:
%%time
from soynlp.word import WordExtractor

sentences = [cor for cor in train_df.Body.values]

word_extractor = WordExtractor(min_count=100,
                               min_cohesion_forward=0.05, 
                               min_right_branching_entropy=0.0)

word_extractor.train(sentences)
words = word_extractor.extract()

training was done. used memory 1.474 Gbory 0.193 Gb
all cohesion probabilities was computed. # words = 20187
all branching entropies was computed # words = 479883
all accessor variety was computed # words = 479883
CPU times: user 1min 7s, sys: 1.16 s, total: 1min 8s
Wall time: 1min 8s


In [20]:
for i in words.items():
    print(i[1])

Scores(cohesion_forward=0, cohesion_backward=0, left_branching_entropy=4.345315345678633, right_branching_entropy=2.1385901204470916, left_accessor_variety=302, right_accessor_variety=97, leftside_frequency=10381, rightside_frequency=948)
Scores(cohesion_forward=0, cohesion_backward=0, left_branching_entropy=1.1438787217183828, right_branching_entropy=5.0325250709063845, left_accessor_variety=8, right_accessor_variety=368, leftside_frequency=0, rightside_frequency=7929)
Scores(cohesion_forward=0, cohesion_backward=0, left_branching_entropy=1.2882736206852, right_branching_entropy=-0.0, left_accessor_variety=19, right_accessor_variety=1, leftside_frequency=524, rightside_frequency=0)
Scores(cohesion_forward=0, cohesion_backward=0, left_branching_entropy=2.5787684112677565, right_branching_entropy=3.185244948924216, left_accessor_variety=37, right_accessor_variety=63, leftside_frequency=252, rightside_frequency=381)
Scores(cohesion_forward=0, cohesion_backward=0, left_branching_entropy=4

Scores(cohesion_forward=0.015031244722175308, cohesion_backward=0, left_branching_entropy=3.399739942882521, right_branching_entropy=2.883631197906592, left_accessor_variety=40, right_accessor_variety=28, leftside_frequency=267, rightside_frequency=0)
Scores(cohesion_forward=0.007053672774444624, cohesion_backward=0, left_branching_entropy=3.1807080206420957, right_branching_entropy=-0.0, left_accessor_variety=29, right_accessor_variety=1, leftside_frequency=174, rightside_frequency=0)
Scores(cohesion_forward=0.031096220291069, cohesion_backward=0, left_branching_entropy=3.155492918915786, right_branching_entropy=2.4322781560465367, left_accessor_variety=36, right_accessor_variety=12, leftside_frequency=297, rightside_frequency=0)
Scores(cohesion_forward=0.12690355329949238, cohesion_backward=0, left_branching_entropy=1.89970840298291, right_branching_entropy=2.875887383157689, left_accessor_variety=14, right_accessor_variety=21, leftside_frequency=150, rightside_frequency=0)
Scores(co

Scores(cohesion_forward=0.05303398058252427, cohesion_backward=0, left_branching_entropy=0.9926198846911294, right_branching_entropy=0.7031467502320108, left_accessor_variety=8, right_accessor_variety=3, leftside_frequency=1311, rightside_frequency=0)
Scores(cohesion_forward=0.1655941655941656, cohesion_backward=0, left_branching_entropy=3.4740287244210357, right_branching_entropy=1.366158847569202, left_accessor_variety=48, right_accessor_variety=4, leftside_frequency=386, rightside_frequency=0)
Scores(cohesion_forward=0, cohesion_backward=0.016901331099959498, left_branching_entropy=1.1291797033082174, right_branching_entropy=4.5851074923597395, left_accessor_variety=10, right_accessor_variety=228, leftside_frequency=0, rightside_frequency=2462)
Scores(cohesion_forward=0.005957446808510639, cohesion_backward=0.0033808665674214524, left_branching_entropy=2.969226433191072, right_branching_entropy=4.432900636063705, left_accessor_variety=23, right_accessor_variety=139, leftside_frequen

Scores(cohesion_forward=0.01978384319472431, cohesion_backward=0, left_branching_entropy=1.833411803600574, right_branching_entropy=-0.0, left_accessor_variety=13, right_accessor_variety=1, leftside_frequency=108, rightside_frequency=0)
Scores(cohesion_forward=0.009828405703697736, cohesion_backward=0, left_branching_entropy=2.9259921088287935, right_branching_entropy=1.2454410537617744, left_accessor_variety=23, right_accessor_variety=4, leftside_frequency=122, rightside_frequency=0)
Scores(cohesion_forward=0.35668276972624796, cohesion_backward=0, left_branching_entropy=3.7629194581552934, right_branching_entropy=1.8875315864452786, left_accessor_variety=159, right_accessor_variety=53, leftside_frequency=3101, rightside_frequency=0)
Scores(cohesion_forward=0.03781038374717833, cohesion_backward=0, left_branching_entropy=2.6059130563927217, right_branching_entropy=0, left_accessor_variety=28, right_accessor_variety=0, leftside_frequency=268, rightside_frequency=0)
Scores(cohesion_forw

Scores(cohesion_forward=0.15764065654349163, cohesion_backward=0.0010470869912210694, left_branching_entropy=2.9979981711792214, right_branching_entropy=4.568782843946597, left_accessor_variety=62, right_accessor_variety=213, leftside_frequency=1796, rightside_frequency=328)
Scores(cohesion_forward=0, cohesion_backward=0.002048891326490637, left_branching_entropy=0.6730116670092565, right_branching_entropy=3.922779110976076, left_accessor_variety=2, right_accessor_variety=85, leftside_frequency=0, rightside_frequency=523)
Scores(cohesion_forward=0, cohesion_backward=0.0005874087754171777, left_branching_entropy=0, right_branching_entropy=2.9682016094868624, left_accessor_variety=0, right_accessor_variety=24, leftside_frequency=0, rightside_frequency=125)
Scores(cohesion_forward=0.0040884119074996806, cohesion_backward=0, left_branching_entropy=2.9648545668552475, right_branching_entropy=1.340198406571469, left_accessor_variety=23, right_accessor_variety=5, leftside_frequency=160, right

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [11]:
def word_score(score):
    import math
    return (score.cohesion_forward * math.exp(score.right_branching_entropy))

print('단어   (빈도수, cohesion, branching entropy)\n')
for word, score in sorted(words.items(), key=lambda x:word_score(x[1]), reverse=True)[:30]:
    print('%s     (%d, %.3f, %.3f)' % (word, 
                                   score.leftside_frequency, 
                                   score.cohesion_forward,
                                   score.right_branching_entropy
                                  ))

단어   (빈도수, cohesion, branching entropy)

함께     (6045, 0.872, 5.376)
먼저     (1737, 0.890, 5.057)
때문에     (7088, 0.610, 5.308)
갑자기     (1059, 0.679, 5.109)
된다.     (1932, 0.681, 5.021)
했다.     (10067, 0.689, 4.984)
과정에서     (2118, 0.583, 5.103)
됐다.     (1808, 0.617, 4.927)
있다.     (29162, 0.525, 5.074)
굉장히     (1084, 0.973, 4.394)
같은     (7479, 0.542, 4.967)
말했다.     (12614, 0.761, 4.626)
때문이다.     (2709, 0.614, 4.787)
년간     (142, 0.477, 5.023)
밝혔다.     (6218, 0.841, 4.446)
너무     (2831, 0.812, 4.448)
곧바로     (507, 0.869, 4.361)
났다.     (235, 0.565, 4.719)
새로운     (1275, 0.538, 4.763)
한다.     (5329, 0.385, 5.091)
냈다.     (432, 0.715, 4.451)
덧붙였다.     (1456, 0.976, 4.118)
셈이다.     (880, 0.904, 4.173)
역시     (2295, 0.358, 5.070)
통해     (6284, 0.395, 4.967)
왔다.     (589, 0.522, 4.682)
것이다.     (5404, 0.465, 4.797)
또는     (1293, 0.448, 4.832)
식으로     (659, 0.356, 5.038)
섰다.     (104, 0.746, 4.298)


In [21]:
# make words to scores 
scores = {}
for word, score in words.items():
    scores[word] = word_score(score)

In [22]:
from soynlp.tokenizer import LTokenizer

mytokenizer = LTokenizer(scores=scores)

In [23]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

#corpus 
corpus = [cor for cor in train_df.Body.values]

# countvectorizer
c_bow = CountVectorizer(tokenizer=mytokenizer, min_df=30, max_df=0.7, lowercase=False)
c_bow_bigram = CountVectorizer(tokenizer=mytokenizer, min_df=30, max_df=0.7, ngram_range=(1, 2), lowercase=False)
c_bow_trigram = CountVectorizer(tokenizer=mytokenizer, min_df=30, max_df=0.7, ngram_range=(1, 3), lowercase=False)

# tfidfvectorizer
t_bow = TfidfVectorizer(tokenizer=mytokenizer, min_df=30, max_df=0.7, lowercase=False)
t_bow_bigram = TfidfVectorizer(tokenizer=mytokenizer, min_df=30, max_df=0.7, ngram_range=(1, 2), lowercase=False)
t_bow_trigram = TfidfVectorizer(tokenizer=mytokenizer, min_df=30, max_df=0.7, ngram_range=(1, 3), lowercase=False)

# fitting
c_bow_feature = c_bow.fit_transform(corpus).todense()
c_bow_bigram_feature = c_bow_bigram.fit_transform(corpus).todense()
c_bow_trigram_feature = c_bow_trigram.fit_transform(corpus).todense()

t_bow_feature = t_bow.fit_transform(corpus).todense()
t_bow_bigram_feature = t_bow_bigram.fit_transform(corpus).todense()
t_bow_trigram_feature = t_bow_trigram.fit_transform(corpus).todense()

del corpus

In [24]:
c_bow_feature.shape, t_bow_feature.shape

((14537, 14043), (14537, 14043))

In [25]:
c_bow_bigram_feature.shape, t_bow_bigram_feature.shape

((14537, 30906), (14537, 30906))

In [26]:
c_bow_trigram_feature.shape, t_bow_trigram_feature.shape

((14537, 32793), (14537, 32793))

In [27]:
%%time
cv = KFold(5, shuffle=True)

# model = MultinomialNB()

features = [c_bow_feature, c_bow_bigram_feature, c_bow_trigram_feature, 
            t_bow_feature, t_bow_bigram_feature, t_bow_trigram_feature]
variations = ["Uni_countvectorizer", "Bi_countvectorizer", "Tri_countvectorizer",
             "Uni_TfIdfvectorizer", "Bi_TfIdfvectorizer", "Tri_TfIdfvectorizer"]
y = [0 if z == '0.0' else 1 for z in train_df.sex.values]

for i, feature in enumerate(features):
    print("{} starts".format(variations[i]))
    model= MultinomialNB().fit(feature, y)
    pred = model.predict(feature)
    scores = cross_val_score(model, feature, y, cv=cv, scoring='accuracy')
    print("Model{} : mean score: {}\n".format(variations[i], np.mean(scores)))


Uni_countvectorizer starts
ModelUni_countvectorizer : mean score: 0.7173406315638058

Bi_countvectorizer starts
ModelBi_countvectorizer : mean score: 0.7176161842424655

Tri_countvectorizer starts
ModelTri_countvectorizer : mean score: 0.714521108040214

Uni_TfIdfvectorizer starts
ModelUni_TfIdfvectorizer : mean score: 0.7208497110565069

Bi_TfIdfvectorizer starts
ModelBi_TfIdfvectorizer : mean score: 0.719336738290963

Tri_TfIdfvectorizer starts
ModelTri_TfIdfvectorizer : mean score: 0.7187186078852497

CPU times: user 2min 30s, sys: 1min 30s, total: 4min 1s
Wall time: 2min 50s


#### 성적이 그나마 좋은 Tfidf_unigram 으로 vectorize한 feature를 사용한 모델 

In [29]:
model = MultinomialNB().fit(t_bow_feature, y)
model 

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [30]:
tokens = t_bow.get_feature_names()

male_token_count = model.feature_count_[0] + model.alpha
female_token_count = model.feature_count_[1] + model.alpha

token_df = pd.DataFrame({"tokens" : tokens,
                          "male" : male_token_count,
                          "female" : female_token_count}).set_index("tokens")

token_df.sample(10) ## Tfidf방식으로 vectorize했기 때문에 실수값으로 나온다 .

female       male
tokens                      
지위       5.768269   7.356545
74년      1.786306   1.710460
‘아       9.341750   6.665963
오빠       6.336868   3.586565
88년      1.741422   2.589549
주민들은     6.380442   7.164333
에.       1.397063   1.466510
싹        1.862382   1.877767
아파트     50.937629  34.552512
가를       3.630569   5.578330

#### 남녀간의 비교 

In [31]:
male_total_count = sum(token_df.male)
female_total_count = sum(token_df.female)

token_df["male_probablility"] = token_df.male / male_total_count
token_df["female_probablility"] = token_df.female / female_total_count
token_df["male_prior"] = token_df.male_probablility / token_df.female_probablility
token_df["female_prior"] = token_df.female_probablility / token_df.male_probablility
token_df.sample(15)

female       male  male_probablility  female_probablility  \
tokens                                                                 
싶어서      3.997056   2.805468           0.000030             0.000043   
1~2      6.025455   4.910486           0.000053             0.000065   
나게       3.881894   3.296820           0.000035             0.000042   
인형       4.908920   3.601357           0.000039             0.000053   
다르다.     4.444180   5.388468           0.000058             0.000048   
실정이다.    3.429908   4.015590           0.000043             0.000037   
결론이      2.671698   3.569018           0.000038             0.000029   
된다는      9.522890   9.575186           0.000102             0.000102   
정확       3.224855   3.127091           0.000033             0.000035   
알려진     11.308396  11.826724           0.000127             0.000121   
않았고,     5.391986   4.544709           0.000049             0.000058   
중에서도     3.615362   3.384891           0.000036             0.000039   
하고도      3.093240   3.017815           0.000032             0.000033   
집값이      3.344055   2.895829           0.000031             0.000036   
가고,      1.728811   1.883199           0.000020             0.000019   

        male_prior  female_prior  
tokens                            
싶어서       0.700447      1.427660  
1~2       0.813289      1.229575  
나게        0.847543      1.179881  
인형        0.732134      1.365870  
다르다.      1.209996      0.826449  
실정이다.     1.168361      0.855900  
결론이       1.333127      0.750116  
된다는       1.003434      0.996578  
정확        0.967700      1.033378  
알려진       1.043695      0.958134  
않았고,      0.841139      1.188865  
중에서도      0.934336      1.070279  
하고도       0.973619      1.027095  
집값이       0.864191      1.157152  
가고,       1.087074      0.919901

In [32]:
token_df[["male_prior", "female_prior"]].sample(10)

male_prior  female_prior
tokens                          
수렴        0.935201      1.069289
시설        0.902132      1.108485
옮긴        0.896752      1.115135
채권        1.149480      0.869958
.1%,      1.613390      0.619813
층에        0.854732      1.169958
보았다.      0.930611      1.074563
수원시       0.835601      1.196743
주인공       0.794416      1.258786
발걸음을      0.685773      1.458208

#### 성별 워드클라우드 생성 

In [33]:
from wordcloud import WordCloud

male_dict = {token: ratio for token, ratio in zip(token_df.index, token_df.male_prior)}
female_dict = {token: ratio for token, ratio in zip(token_df.index, token_df.female_prior)}

male_wordcloud = WordCloud(font_path="/Library/Fonts/AppleGothic.ttf",
                   background_color="white",
                   width=800,
                   height=400).generate_from_frequencies(male_dict)

female_wordcloud = WordCloud(font_path="/Library/Fonts/AppleGothic.ttf",
                   background_color="white",
                   width=800,
                   height=400).generate_from_frequencies(female_dict)

In [34]:
plt.figure(figsize=(17, 9), dpi=700)
plt.imshow(male_wordcloud)
plt.axis("off")

plt.savefig("male_prefered_words.png", transparent=True, bbox_inches="tight")

In [35]:
plt.figure(figsize=(17, 9), dpi=700)
plt.imshow(female_wordcloud)
plt.axis("off")

plt.savefig("female_prefered_words.png", transparent=True, bbox_inches="tight")